In [4]:
import os

os.chdir('/Users/gabriele/PycharmProjects/RecSys')
##Best Config is: 'topK': 192, 'l1_ratio': 0.1412276559017871, 'alpha': 0.006804121317480965, 'workers': 10

In [5]:
from src.HyperparameterTuning.SearchAbstractClass import SearchInputRecommenderArgs
from src.Recommenders.SLIM.SLIMElasticNetRecommender import MultiThreadSLIM_SLIMElasticNetRecommender
from Utils.utils import create_URM,create_ICM_with_events, combine_matrices
from src.Evaluation.Evaluator import EvaluatorHoldout
from src.Data_manager.split_functions.split_train_validation_random_holdout import split_train_in_two_percentage_global_sample
from skopt.space import Real, Integer, Categorical


URM = create_URM()
ICM = create_ICM_with_events()


URM_train_validation,URM_test = split_train_in_two_percentage_global_sample(URM,train_percentage=0.85)
URM_train, URM_validation = split_train_in_two_percentage_global_sample(URM_train_validation,train_percentage=0.85)

StackedMatrices = combine_matrices(ICM=ICM, URM=URM_train)

evaluator_test = EvaluatorHoldout(URM_test, cutoff_list=[10])
evaluator_validation = EvaluatorHoldout(URM_validation, cutoff_list=[10])


from src.HyperparameterTuning.SearchBayesianSkopt import SearchBayesianSkopt
hyperparameters_range_dictionary = {
    "topK": Integer(10,500),
    "l1_ratio": Real(0.001,1),
    "alpha": Real(0.0001,0.01),
    "workers": Categorical([10])
}
recommender_input_args = SearchInputRecommenderArgs(
    CONSTRUCTOR_POSITIONAL_ARGS = [StackedMatrices],     # For a CBF model simply put [URM_train, ICM_train]
    CONSTRUCTOR_KEYWORD_ARGS = {},
    FIT_POSITIONAL_ARGS = [],
    FIT_KEYWORD_ARGS = {}
)
recommender_input_args_last_test = SearchInputRecommenderArgs(
    CONSTRUCTOR_POSITIONAL_ARGS = [URM_train_validation],     # For a CBF model simply put [URM_train_validation, ICM_train]
    CONSTRUCTOR_KEYWORD_ARGS = {},
    FIT_POSITIONAL_ARGS = [],
    FIT_KEYWORD_ARGS = {}
)

tuning_class = SearchBayesianSkopt(recommender_class=MultiThreadSLIM_SLIMElasticNetRecommender,
                                   evaluator_validation=evaluator_validation,
                                   evaluator_test=evaluator_test)

n_cases = 100
n_random_starts = n_cases*0.3
output_folder_path = "logs/"

tuning_class.search(recommender_input_args=recommender_input_args,
                    hyperparameter_search_space=hyperparameters_range_dictionary,
                    metric_to_optimize="MAP",
                    cutoff_to_optimize= 10,
                    n_cases= n_cases,
                    n_random_starts=n_random_starts,
                    output_folder_path=output_folder_path,
                    output_file_name_root=MultiThreadSLIM_SLIMElasticNetRecommender.RECOMMENDER_NAME,
                    save_model="best"
                    )
## Best config is 95: {'topK': 367, 'l1_ratio': 0.001, 'alpha': 0.0051965845279935575, 'workers': 10}

EvaluatorHoldout: Ignoring 13633 ( 0.1%) Users that have less than 1 test interactions
EvaluatorHoldout: Ignoring 13634 ( 0.1%) Users that have less than 1 test interactions
Iteration No: 1 started. Evaluating function at random point.
SearchBayesianSkopt: Testing config: {'topK': 431, 'l1_ratio': 0.6878069576760028, 'alpha': 0.009161221179323498, 'workers': 10}
SLIMElasticNetRecommender: URM Detected 10245 ( 2.8%) users with no interactions.



 25%|█████████▏                           | 4456/18059 [00:32<01:55, 118.03it/s]


 46%|█████████████████▍                    | 8264/18059 [01:03<02:12, 73.80it/s]


 68%|████████████████████████▍           | 12264/18059 [01:36<00:40, 141.46it/s]


 87%|███████████████████████████████▍    | 15784/18059 [02:07<00:21, 106.77it/s]


...

 40%|███████████████▏                      | 7208/18059 [05:21<06:02, 29.92it/s]

 40%|███████████████▏                      | 7240/18059 [05:22<04:52, 37.04it/s]

 40%|███████████████▎                      | 7272/18059 [05:23<05:14, 34.27it/s]

 40%|███████████████▎                      | 7304/18059 [05:23<04:35, 39.01it/s]

 41%|███████████████▍                      | 7336/18059 [05:26<08:08, 21.96it/s]

 41%|███████████████▌                      | 7368/18059 [05:32<14:47, 12.04it/s]

 41%|███████████████▌                      | 7400/18059 [05:34<13:23, 13.26it/s]

 41%|███████████████▋                      | 7464/18059 [05:34<08:01, 22.02it/s]

 42%|███████████████▊                      | 7496/18059 [05:35<06:33, 26.83it/s]

 42%|███████████████▊                      | 7528/18059 [05:35<05:39, 31.03it/s]

 42%|███████████████▉                      | 7560/18059 [05:35<04:20, 40.27it/s]

 42%|███████████████▉                      | 7592/18059 [05:37<05:32, 31.48it/s]

 42%|███████████

 58%|█████████████████████▍               | 10440/18059 [07:43<03:51, 32.90it/s]

 58%|█████████████████████▍               | 10472/18059 [07:44<04:08, 30.51it/s]

 58%|█████████████████████▌               | 10504/18059 [07:45<03:46, 33.35it/s]

 58%|█████████████████████▌               | 10536/18059 [07:48<07:07, 17.58it/s]

 59%|█████████████████████▋               | 10568/18059 [07:52<08:48, 14.17it/s]

 59%|█████████████████████▋               | 10600/18059 [07:53<07:17, 17.05it/s]

 59%|█████████████████████▊               | 10632/18059 [07:53<05:40, 21.82it/s]

 59%|█████████████████████▊               | 10664/18059 [07:54<05:12, 23.70it/s]

 59%|█████████████████████▉               | 10696/18059 [07:55<04:54, 24.97it/s]

 59%|█████████████████████▉               | 10728/18059 [07:56<03:57, 30.93it/s]

 60%|██████████████████████               | 10760/18059 [07:56<03:24, 35.71it/s]

 60%|██████████████████████               | 10792/18059 [07:58<04:26, 27.29it/s]

 60%|███████████

 75%|███████████████████████████▊         | 13576/18059 [10:04<03:20, 22.37it/s]

 76%|███████████████████████████▉         | 13640/18059 [10:05<02:09, 34.14it/s]

 76%|████████████████████████████         | 13672/18059 [10:07<03:02, 24.07it/s]

 76%|████████████████████████████         | 13704/18059 [10:08<02:25, 29.97it/s]

 76%|████████████████████████████▏        | 13736/18059 [10:11<03:59, 18.06it/s]

 76%|████████████████████████████▏        | 13768/18059 [10:14<04:41, 15.22it/s]

 77%|████████████████████████████▎        | 13832/18059 [10:16<03:15, 21.59it/s]

 77%|████████████████████████████▍        | 13864/18059 [10:18<03:37, 19.31it/s]

 77%|████████████████████████████▍        | 13896/18059 [10:18<02:57, 23.42it/s]

 77%|████████████████████████████▌        | 13928/18059 [10:19<02:15, 30.39it/s]

 77%|████████████████████████████▌        | 13960/18059 [10:19<01:54, 35.77it/s]

 77%|████████████████████████████▋        | 13992/18059 [10:22<03:03, 22.19it/s]

 78%|███████████

 93%|██████████████████████████████████▎  | 16744/18059 [12:34<00:59, 22.16it/s]

 93%|██████████████████████████████████▎  | 16776/18059 [12:34<00:44, 28.62it/s]

 93%|██████████████████████████████████▍  | 16808/18059 [12:35<00:36, 34.10it/s]

 93%|██████████████████████████████████▌  | 16872/18059 [12:37<00:37, 31.59it/s]

 94%|██████████████████████████████████▋  | 16904/18059 [12:40<00:52, 22.16it/s]

 94%|██████████████████████████████████▋  | 16936/18059 [12:44<01:12, 15.40it/s]

 94%|██████████████████████████████████▊  | 16968/18059 [12:44<00:56, 19.45it/s]

 94%|██████████████████████████████████▊  | 17000/18059 [12:46<00:54, 19.35it/s]

 94%|██████████████████████████████████▉  | 17032/18059 [12:46<00:42, 24.33it/s]

 94%|██████████████████████████████████▉  | 17064/18059 [12:48<00:39, 25.31it/s]

 95%|███████████████████████████████████  | 17096/18059 [12:49<00:35, 26.82it/s]

 95%|███████████████████████████████████  | 17128/18059 [12:49<00:29, 31.92it/s]

 95%|███████████

EvaluatorHoldout: Processed 13634 (100.0%) in 19.62 sec. Users per second: 695
SearchBayesianSkopt: Config 99 is suboptimal. Config: {'topK': 436, 'l1_ratio': 0.001, 'alpha': 0.004429414087650706, 'workers': 10} - results: PRECISION: 0.2189306, PRECISION_RECALL_MIN_DEN: 0.2225568, RECALL: 0.0623899, MAP: 0.1035579, MAP_MIN_DEN: 0.1053221, MRR: 0.4364602, NDCG: 0.2265633, F1: 0.0971067, HIT_RATE: 0.8906410, ARHR_ALL_HITS: 0.6711444, NOVELTY: 0.0054820, AVERAGE_POPULARITY: 0.5201237, DIVERSITY_MEAN_INTER_LIST: 0.8936378, DIVERSITY_HERFINDAHL: 0.9893572, COVERAGE_ITEM: 0.0629603, COVERAGE_ITEM_CORRECT: 0.0396478, COVERAGE_USER: 0.9988278, COVERAGE_USER_CORRECT: 0.8895971, DIVERSITY_GINI: 0.0086172, SHANNON_ENTROPY: 7.5354321, RATIO_DIVERSITY_HERFINDAHL: 0.9897181, RATIO_DIVERSITY_GINI: 0.0322147, RATIO_SHANNON_ENTROPY: 0.6033230, RATIO_AVERAGE_POPULARITY: 3.2725774, RATIO_NOVELTY: 0.6959335, 

Iteration No: 100 ended. Search finished for the next optimal point.
Time taken: 826.7862
Functi

In [7]:
recommender_new= MultiThreadSLIM_SLIMElasticNetRecommender(URM_train= StackedMatrices)
recommender_new.fit(topK= 367, l1_ratio = 0.001, alpha = 0.0051965845279935575, workers=10 )

SLIMElasticNetRecommender: URM Detected 10245 ( 2.8%) users with no interactions.



 21%|████████▏                             | 3880/18059 [02:40<16:18, 14.49it/s]


 41%|███████████████▌                      | 7368/18059 [05:08<15:00, 11.88it/s]


 66%|████████████████████████▎            | 11880/18059 [08:30<05:49, 17.66it/s]


 85%|███████████████████████████████▎     | 15304/18059 [11:02<01:52, 24.49it/s]


100%|██████████████████████████████████▉| 18056/18059 [2:39:29<00:01,  1.89it/s]

 99%|████████████████████████████████████▊| 17968/18059 [13:04<00:03, 28.05it/s]

In [10]:
from Utils.utils import create_ICM, combine_matrices

ICM_no_events = create_ICM()
URM_stacked_train = combine_matrices(ICM=ICM_no_events, URM= URM_train)
##SLIMELASTICNET Recommender
SLIME_recommender = MultiThreadSLIM_SLIMElasticNetRecommender(URM_train=URM_stacked_train)
SLIME_recommender.fit(topK=420, l1_ratio=0.06061216785568925, alpha=0.00554982938879437, workers = 10)



  0%|                                                 | 0/18059 [00:00<?, ?it/s]

  0%|                                       | 8/18059 [00:09<5:47:22,  1.15s/it]

  0%|                                        | 40/18059 [00:09<54:12,  5.54it/s]

  1%|▏                                      | 104/18059 [00:09<16:17, 18.37it/s]

  1%|▎                                      | 136/18059 [00:09<11:28, 26.02it/s]

  1%|▎                                      | 168/18059 [00:10<08:21, 35.67it/s]

  1%|▍                                      | 200/18059 [00:10<06:12, 47.89it/s]

  2%|▋                                      | 296/18059 [00:11<04:39, 63.57it/s]

  2%|▋                                      | 328/18059 [00:16<14:14, 20.76it/s]

  2%|▊                                      | 360/18059 [00:17<12:07, 24.34it/s]

  2%|▊                                      | 392/18059 [00:18<10:33, 27.87it/s]

  2%|▉                                      | 424/18059 [00:18<08:12, 35.81it/s]

  3%|█        

 19%|███████▎                              | 3496/18059 [01:42<06:19, 38.36it/s]

 20%|███████▍                              | 3528/18059 [01:45<10:26, 23.21it/s]

 20%|███████▍                              | 3560/18059 [01:46<08:32, 28.31it/s]

 20%|███████▌                              | 3592/18059 [01:46<06:14, 38.67it/s]

 20%|███████▋                              | 3624/18059 [01:48<08:39, 27.79it/s]

 20%|███████▋                              | 3656/18059 [01:48<06:17, 38.12it/s]

 20%|███████▊                              | 3688/18059 [01:48<04:44, 50.52it/s]

 21%|███████▉                              | 3752/18059 [01:49<05:03, 47.11it/s]

 21%|███████▉                              | 3784/18059 [01:50<04:44, 50.14it/s]

 21%|████████                              | 3816/18059 [01:51<06:27, 36.76it/s]

 21%|████████                              | 3848/18059 [01:54<09:53, 23.94it/s]

 22%|████████▏                             | 3912/18059 [01:55<06:55, 34.01it/s]

 22%|████████▎  

 38%|██████████████▋                       | 6952/18059 [03:26<07:19, 25.29it/s]

 39%|██████████████▊                       | 7016/18059 [03:27<05:04, 36.26it/s]

 39%|██████████████▊                       | 7048/18059 [03:29<07:09, 25.64it/s]

 39%|██████████████▉                       | 7080/18059 [03:30<06:32, 27.98it/s]

 39%|██████████████▉                       | 7112/18059 [03:30<04:55, 37.03it/s]

 40%|███████████████                       | 7144/18059 [03:31<04:23, 41.35it/s]

 40%|███████████████                       | 7176/18059 [03:31<03:44, 48.57it/s]

 40%|███████████████▏                      | 7208/18059 [03:32<03:40, 49.19it/s]

 40%|███████████████▏                      | 7240/18059 [03:33<04:34, 39.41it/s]

 40%|███████████████▎                      | 7272/18059 [03:36<07:49, 22.99it/s]

 40%|███████████████▎                      | 7304/18059 [03:36<05:43, 31.31it/s]

 41%|███████████████▍                      | 7336/18059 [03:37<05:13, 34.17it/s]

 41%|███████████

 57%|█████████████████████▏               | 10344/18059 [05:08<04:25, 29.01it/s]

 57%|█████████████████████▎               | 10376/18059 [05:08<03:19, 38.48it/s]

 58%|█████████████████████▍               | 10440/18059 [05:09<02:41, 47.06it/s]

 58%|█████████████████████▍               | 10472/18059 [05:11<03:09, 40.10it/s]

 58%|█████████████████████▌               | 10504/18059 [05:14<05:42, 22.07it/s]

 59%|█████████████████████▋               | 10568/18059 [05:15<04:29, 27.84it/s]

 59%|█████████████████████▋               | 10600/18059 [05:17<04:33, 27.28it/s]

 59%|█████████████████████▊               | 10632/18059 [05:17<03:53, 31.84it/s]

 59%|█████████████████████▊               | 10664/18059 [05:18<03:31, 34.91it/s]

 59%|█████████████████████▉               | 10696/18059 [05:18<03:13, 38.05it/s]

 59%|█████████████████████▉               | 10728/18059 [05:19<02:46, 44.11it/s]

 60%|██████████████████████               | 10760/18059 [05:19<02:25, 50.08it/s]

 60%|███████████

 75%|███████████████████████████▊         | 13576/18059 [06:45<02:17, 32.55it/s]

 76%|███████████████████████████▉         | 13640/18059 [06:46<01:41, 43.39it/s]

 76%|████████████████████████████         | 13672/18059 [06:47<01:38, 44.65it/s]

 76%|████████████████████████████         | 13704/18059 [06:47<01:37, 44.70it/s]

 76%|████████████████████████████▏        | 13736/18059 [06:49<02:07, 33.89it/s]

 76%|████████████████████████████▏        | 13768/18059 [06:51<02:44, 26.07it/s]

 76%|████████████████████████████▎        | 13800/18059 [06:51<02:11, 32.32it/s]

 77%|████████████████████████████▎        | 13832/18059 [06:53<02:29, 28.26it/s]

 77%|████████████████████████████▍        | 13864/18059 [06:53<02:12, 31.64it/s]

 77%|████████████████████████████▍        | 13896/18059 [06:54<01:45, 39.50it/s]

 77%|████████████████████████████▌        | 13928/18059 [06:55<01:48, 38.18it/s]

 77%|████████████████████████████▌        | 13960/18059 [06:55<01:22, 49.76it/s]

 77%|███████████

 93%|██████████████████████████████████▍  | 16808/18059 [08:19<00:39, 31.72it/s]

 93%|██████████████████████████████████▌  | 16840/18059 [08:20<00:34, 35.48it/s]

 93%|██████████████████████████████████▌  | 16872/18059 [08:21<00:31, 37.17it/s]

 94%|██████████████████████████████████▋  | 16904/18059 [08:22<00:32, 35.95it/s]

 94%|██████████████████████████████████▋  | 16936/18059 [08:23<00:40, 27.90it/s]

 94%|██████████████████████████████████▊  | 16968/18059 [08:24<00:34, 31.70it/s]

 94%|██████████████████████████████████▊  | 17000/18059 [08:25<00:36, 29.19it/s]

 94%|██████████████████████████████████▉  | 17032/18059 [08:26<00:27, 37.56it/s]

 94%|██████████████████████████████████▉  | 17064/18059 [08:26<00:20, 48.76it/s]

 95%|███████████████████████████████████  | 17096/18059 [08:28<00:30, 31.40it/s]

 95%|███████████████████████████████████  | 17128/18059 [08:29<00:32, 28.62it/s]

 95%|███████████████████████████████████▏ | 17160/18059 [08:30<00:27, 32.37it/s]

 95%|███████████

In [12]:
result_df, _ = evaluator_test.evaluateRecommender(recommender_new)
print(result_df.loc[10])

EvaluatorHoldout: Processed 13633 (100.0%) in 18.81 sec. Users per second: 725
PRECISION                     0.259539
PRECISION_RECALL_MIN_DEN      0.262316
RECALL                        0.062622
MAP                           0.132227
MAP_MIN_DEN                   0.133496
MRR                           0.493931
NDCG                          0.268978
F1                            0.100899
HIT_RATE                      0.929729
ARHR_ALL_HITS                  0.80373
NOVELTY                        0.00547
AVERAGE_POPULARITY            0.525978
DIVERSITY_MEAN_INTER_LIST     0.888167
DIVERSITY_HERFINDAHL           0.98881
COVERAGE_ITEM                 0.062074
COVERAGE_ITEM_CORRECT         0.038817
COVERAGE_USER                 0.998755
COVERAGE_USER_CORRECT         0.928571
DIVERSITY_GINI                0.008125
SHANNON_ENTROPY               7.451144
RATIO_DIVERSITY_HERFINDAHL    0.989171
RATIO_DIVERSITY_GINI          0.030375
RATIO_SHANNON_ENTROPY         0.596574
RATIO_AVERAGE_POPULARITY

In [13]:
result_df, _ = evaluator_test.evaluateRecommender(SLIME_recommender)
print(result_df.loc[10])

EvaluatorHoldout: Processed 13633 (100.0%) in 11.45 sec. Users per second: 1190
PRECISION                     0.260266
PRECISION_RECALL_MIN_DEN      0.263108
RECALL                         0.06336
MAP                           0.131735
MAP_MIN_DEN                   0.132918
MRR                           0.493732
NDCG                          0.269075
F1                             0.10191
HIT_RATE                      0.930683
ARHR_ALL_HITS                 0.802578
NOVELTY                       0.005653
AVERAGE_POPULARITY            0.496493
DIVERSITY_MEAN_INTER_LIST     0.933848
DIVERSITY_HERFINDAHL          0.993378
COVERAGE_ITEM                 0.116618
COVERAGE_ITEM_CORRECT         0.068332
COVERAGE_USER                 0.998755
COVERAGE_USER_CORRECT         0.929524
DIVERSITY_GINI                 0.01643
SHANNON_ENTROPY               8.395841
RATIO_DIVERSITY_HERFINDAHL    0.993752
RATIO_DIVERSITY_GINI          0.063426
RATIO_SHANNON_ENTROPY         0.674756
RATIO_AVERAGE_POPULARIT

In [5]:
from src.HyperparameterTuning.SearchAbstractClass import SearchInputRecommenderArgs
from src.Recommenders.SLIM.SLIMElasticNetRecommender import MultiThreadSLIM_SLIMElasticNetRecommender
from Utils.utils import create_URM,create_ICM, combine_matrices

URM = create_URM()
ICM = create_ICM()

ICMCombined = combine_matrices(ICM=ICM, URM=URM)
recommender_tuned = MultiThreadSLIM_SLIMElasticNetRecommender(ICMCombined)
recommender_tuned.fit(topK=420, l1_ratio = 0.06061216785568925, alpha= 0.00554982938879437, workers = 10)

100%|████████████████████████████████████▉| 18056/18059 [11:10<00:00, 49.38it/s]

In [4]:
def load_users_for_submission():
    return pd.read_csv("/Users/gabriele/PycharmProjects/RecSys/data/utils-csv/data_target_users_test.csv",
                        names = ['userID'],
                        header = 0)

In [5]:
import pandas as pd
users_to_recommend = load_users_for_submission()
submission =[]
for user in users_to_recommend["userID"].values:
    submission.append((user,recommender_tuned.recommend(user,10)))

In [6]:
def write_submission(submission):
    with open("./SLIMStacked.csv", "w") as f:
        f.write("user_id,item_list\n")
        for user_id, items in submission:
            f.write(f"{user_id},{' '.join([str(item) for item in items])}\n")

In [7]:
write_submission(submission)